### 변수 초기화 - Initialization of variables

In [21]:
# Clear all global variables except those starting with an underscore
all = [var for var in globals() if var[0] != '_']
for var in all:
    del globals()[var]
del var, all

### 모듈 불러오기 Importing modules

In [22]:
# ------------------------------------------------- 기본 모듈 import
import os, sys # 운영체제 및 시스템 모듈
from importlib import reload # 모듈 리로드용
import numpy as np # 수치해석 모듈
import pandas as pd # 데이터프레임 모듈
from scipy.sparse import lil_matrix, csr_matrix # 희소행렬 모듈
from scipy.sparse.linalg import spsolve # 희소행렬 선형방정식 풀이 모듈
import meshio # mesh 입출력 모듈

# ------------------------------------------------- FEM 전용 모듈 import
# mesh 전처리 모듈 import
import fem_process_gmsh
reload(fem_process_gmsh)

# global material property 적용을 위한 모듈 import
import fem_global_mat_prop
reload(fem_global_mat_prop)

# boundary condition 적용을 위한 모듈 import
import fem_dirichlet_bc
reload(fem_dirichlet_bc)

<module 'fem_dirichlet_bc' from 'c:\\Users\\opew4\\Desktop\\files_fem\\fem_dirichlet_bc.py'>

### Mesh 데이터 전처리 - Mesh data import

In [23]:
# file_gmsh = "C:\\Users\\opew4\\Desktop\\files_fem\\files_gmsh\\square_hex.msh"  # .msh 파일 경로
file_gmsh = "C:\\Users\\opew4\\Desktop\\files_fem\\files_gmsh\\simple_bracket.msh"  # .msh 파일 경로
curated_data_msh = fem_process_gmsh.run_pipeline(file_gmsh)

print('\nmain key check:')
print(f'curated_data_msh.keys() : {list(curated_data_msh.keys())}')

No more sections found.

data_nodes shape: (14591, 4)
data_elements shape: (61167, 6)

BC summary:
disp_BC: dim= 2 physical_tag= 107 entity= 33 num_nodes= 441
traction_BC_ru: dim= 2 physical_tag= 108 entity= 35 num_nodes= 228
traction_BC_lb: dim= 2 physical_tag= 109 entity= 34 num_nodes= 228

main key check:
curated_data_msh.keys() : ['dict_section', 'info_BC', 'data_nodes', 'data_elements', 'remaining_text_lines']


In [20]:
curated_data_msh['dict_section']['Nodes']

['213 14591 1 14591',
 '0 1 0 1',
 '1',
 '-214.0402215813 -63.96 -15',
 '0 2 0 1',
 '2',
 '-225.0000163827 -74.91979428949 -15',
 '0 3 0 1',
 '3',
 '-225.0000163827 -74.91979428949 15',
 '0 4 0 1',
 '4',
 '-214.0402215813 -63.96 15',
 '0 5 0 1',
 '5',
 '-225.0000173206 -94.99999859876 15',
 '0 6 0 1',
 '6',
 '-225.0000173206 -94.99999859876 -15',
 '0 7 0 1',
 '7',
 '-195.0000173206 -125 -15',
 '0 8 0 1',
 '8',
 '-195.0000173206 -125 15',
 '0 9 0 1',
 '9',
 '-24.6651694558 -125 15',
 '0 10 0 1',
 '10',
 '-24.6651694558 -125 -15',
 '0 11 0 1',
 '11',
 '-0.262144282188 -116.6937274926 -15',
 '0 12 0 1',
 '12',
 '-0.262144282188 -116.6937274926 15',
 '0 13 0 1',
 '13',
 '211.35266574885 46.242031247095 15',
 '0 14 0 1',
 '14',
 '211.35266574885 46.242031247095 -15',
 '0 15 0 1',
 '15',
 '225.00001872193 73.974042803128 -15',
 '0 16 0 1',
 '16',
 '225.00001872193 73.974042803128 15',
 '0 17 0 1',
 '17',
 '225.00001872193 95 15',
 '0 18 0 1',
 '18',
 '225.00001872193 95 -15',
 '0 19 0 1',
 '

In [4]:
df_elements = curated_data_msh['data_elements']
df_elements

elem_tag  elem_type_int  node_1  node_2  node_3  node_4 elem_type
0             1              2     991      65    4091      -1      tri3
1             2              2    4097      65    1038      -1      tri3
2             3              2    4091      65    1039      -1      tri3
3             4              2    1039      65    4097      -1      tri3
4             5              2    4088      66    1043      -1      tri3
...         ...            ...     ...     ...     ...     ...       ...
61162     61163              4    3226    3099   11434    3134    tetra4
61163     61164              4    5443   12670    6711   13624    tetra4
61164     61165              4    5443    6711   12670      90    tetra4
61165     61166              4    1244    6711   12670   13624    tetra4
61166     61167              4    1244   12670    6711      90    tetra4

[61167 rows x 7 columns]

In [5]:
df_nodes = curated_data_msh['data_nodes']
df_nodes

node_tag           x           y          z
0           1.0 -214.040222  -63.960000 -15.000000
1           2.0 -225.000016  -74.919794 -15.000000
2           3.0 -225.000016  -74.919794  15.000000
3           4.0 -214.040222  -63.960000  15.000000
4           5.0 -225.000017  -94.999999  15.000000
...         ...         ...         ...        ...
14586   14587.0  158.497867   87.596778   4.059491
14587   14588.0   37.376988   86.743349   9.496878
14588   14589.0 -117.122793  105.146093  10.322983
14589   14590.0 -124.228105   78.526216  10.128234
14590   14591.0    8.405312   29.973087  -2.009197

[14591 rows x 4 columns]

In [6]:
# elements, nodes 정보 추출
ndarray_elements = np.array(df_elements.iloc[:, :-1])
ndarray_nodes = np.array(df_nodes)

### Global material properties matrix 생성

In [7]:
# Linear elasticity tensor (6x6)
C = np.zeros((6, 6))

# Isotropic material properties
E = 210e3  # Young's modulus N/mm2
nu = 0.3   # Poisson's ratio

# Lame parameters
lam = E * nu / ((1 + nu) * (1 - 2 * nu))
mu  = E / (2 * (1 + nu))   # shear modulus

C = np.array([
    [lam + 2 * mu, lam,          lam,          0,  0,  0],
    [lam,          lam + 2 * mu, lam,          0,  0,  0],
    [lam,          lam,          lam + 2 * mu, 0,  0,  0],
    [0,            0,            0,            mu, 0,  0],
    [0,            0,            0,            0,  mu, 0],
    [0,            0,            0,            0,  0, mu]
])

Kg = fem_global_mat_prop.global_mat_prop(ndarray_nodes, ndarray_elements, C)

Element 1597 : Adding element material property matrix to Global material property matrix
Element 1598 : Adding element material property matrix to Global material property matrix
Element 1599 : Adding element material property matrix to Global material property matrix
Element 1600 : Adding element material property matrix to Global material property matrix
Element 1601 : Adding element material property matrix to Global material property matrix
Element 1602 : Adding element material property matrix to Global material property matrix
Element 1603 : Adding element material property matrix to Global material property matrix
Element 1604 : Adding element material property matrix to Global material property matrix
Element 1605 : Adding element material property matrix to Global material property matrix
Element 1606 : Adding element material property matrix to Global material property matrix
Element 1607 : Adding element material property matrix to Global material property matrix
Element 16

In [8]:
np.min(Kg.diagonal())

np.float64(160872.16222958878)

### Kd = F에 B.C 적용

In [9]:
# # Beam 예제용 Dirichlet BC 및 Force 벡터 적용 코드
# # (Cantilever beam 예제에서만 사용. 일반 FEM에서는 다른 BC 처리 필요
# # ----------------------------
# # 1) BC 노드 태그 가져오기
# # ----------------------------
# disp_nodes = None
# load_nodes = None

# info_BC = curated_data_msh['info_BC']

# for bc in info_BC:
#     if bc["name"] == "displacementBC":
#         disp_nodes = np.array(bc["node_tags"], dtype=int)
#     elif bc["name"] == "loadBC":
#         load_nodes = np.array(bc["node_tags"], dtype=int)

# if disp_nodes is None or load_nodes is None:
#     raise ValueError("displacementBC 또는 loadBC를 data_BC에서 찾지 못했습니다.")

# ndof = ndarray_nodes.shape[0] * 3

# # ----------------------------
# # 2) Force vector 만들기
# # ----------------------------
# F = np.zeros(ndof)

# # 총 하중 (N). 50x50x500 cantilever 기준으로 10kN이면 꽤 큰 하중이지만 변형은 과도하진 않음(선형 범위 가정).
# Fy_total = -1.0e4  # -10,000 N (아래방향)

# fy_each = Fy_total / len(load_nodes)

# for tag_node in load_nodes:
#     dof_y = (tag_node - 1) * 3 + 1  # y방향 DOF: [x=0, y=1, z=2]
#     F[dof_y] += fy_each

# # 3) Dirichlet BC(u=v=w=0) 적용
# Kg, F = fem_dirichlet_bc.dirichlet_bc(Kg, F, disp_nodes)


In [10]:
# Bracket 예제용 Dirichlet BC 및 Force 벡터 적용 코드
# (Bracket 예제에서만 사용. 일반 FEM에서는 다른 BC 처리 필요)

# ----------------------------
# 1) BC 노드 태그 가져오기
# ----------------------------
disp_nodes = None
load_nodes = None

info_BC = curated_data_msh['info_BC']

for bc in info_BC:
    if bc["name"] == "disp_BC":
        disp_nodes = np.array(bc["node_tags"], dtype=int)
    elif bc["name"] == "traction_BC_ru":
        load_nodes_ru = np.array(bc["node_tags"], dtype=int)
    elif bc["name"] == "traction_BC_lb":
        load_nodes_lb = np.array(bc["node_tags"], dtype=int)

if disp_nodes is None or load_nodes_ru is None or load_nodes_lb is None:
    raise ValueError("displacementBC 또는 loadBC를 data_BC에서 찾지 못했습니다.")

ndof = ndarray_nodes.shape[0] * 3

# ----------------------------
# 2) Force vector 만들기
# ----------------------------
F = np.zeros(ndof)

# Right Upper 하중 (N)
Fy_total = 1.0e4  # 10,000 N (+y방향)

fy_each = Fy_total / len(load_nodes_ru)

for tag_node in load_nodes_ru:
    dof_y = (tag_node - 1) * 3 + 1  # y방향 DOF: [x=0, y=1, z=2]
    F[dof_y] += fy_each

# Left Bottom 하중 (N)
Fx_total = 1.0e4  # 10,000 N (+x방향)

fx_each = Fx_total / len(load_nodes_lb)

for tag_node in load_nodes_lb:
    dof_x = (tag_node - 1) * 3 + 0  # x방향 DOF: [x=0, y=1, z=2]
    F[dof_x] += fx_each

# ----------------------------
# 3) Dirichlet BC(u=v=w=0) 적용
Kg, F = fem_dirichlet_bc.dirichlet_bc(Kg, F, disp_nodes)


### Solve

In [11]:
d = spsolve(Kg, F)
disp = d.reshape((-1, 3)) # 변위 벡터 d의 shape은 (ndof,). 필요하면 (nnode,3)으로 reshape:

### 결과 VTU 파일로 mesh와 함께 같이 export

In [12]:
# disp: (nnode,3) or (ndof,) -> (nnode,3)
if disp.ndim == 1:
    disp_vec = disp.reshape((-1, 3))
else:
    disp_vec = disp

mesh = meshio.read(file_gmsh)
# ------------------ 원본 gmsh 파일에 displacment 필드 추가하여 저장
# mesh.points: (nnode,3)
# disp_vec:    (nnode,3)  <-- 이 둘의 노드 순서가 같아야 함
assert mesh.points.shape[0] == disp_vec.shape[0], \
    f"node mismatch: mesh has {mesh.points.shape[0]} nodes, disp has {disp_vec.shape[0]}"

mesh.point_data = mesh.point_data or {}
mesh.point_data["disp"] = disp_vec               # 벡터 필드
mesh.point_data["disp_mag"] = np.linalg.norm(disp_vec, axis=1)  # 크기 스칼라

mesh_solved_path = "files_paraview\\result_simple_bracket.vtu" # ParaView에서 열 파일
meshio.write(mesh_solved_path, mesh)
print("Wrote:", mesh_solved_path)

Info: VTU format cannot write cell_sets. Converting them to cell_data...

Wrote: files_paraview\result_simple_bracket.vtu
